In [2]:
import pandas as pd
from datetime import datetime
import numpy as np
from pyomo.environ import *
import pyomo
import plotly.graph_objects as go
from pyomo.core.expr.current import evaluate_expression as evaluate

In [3]:
# Time range
T = pd.date_range('2017-01-01T00:00','2019-12-31T23:00',freq='H')
#T = pd.date_range('2018-01-01T00:00','2018-12-31T23:00',freq='H')

In [4]:
# Wind and solar availability 
df_capfactor = pd.read_csv('data/windcapacityfacotor.csv')
df_capfactor = df_capfactor.set_index(df_capfactor['HourUTC'])
# Regulating prices and volume (mFRR)
df_reg = pd.read_csv('data/regulating-power-dk1_2017-2019_hourly_dkk.csv',sep=';',decimal=',')
df_reg = df_reg.set_index(pd.date_range('2017-01-01T00:00','2020-01-01T02:00',freq='H'))
# mFRR prices
df_mfrr=pd.read_csv('data/mfrrreservesdk1.csv',sep=',')
df_mfrr = df_mfrr.set_index(df_mfrr['HourUTC'])
# mFRR percent dispatch
df_mfrr_volume_fraction = pd.DataFrame(index=T,
             data=(df_reg['Volume up'][t.strftime('%Y-%m-%d %H:%M:%S')] / df_mfrr['mFRR_UpPurchased'][t.strftime("%Y-%m-%d %H:%M")] for t in T))
# FCR data 
df_fcr = pd.read_csv('data/fcrreservesdk1.csv')
df_fcr = df_fcr.set_index(df_fcr['HourUTC'])
# aFRR data
df_afrr = pd.read_csv('data/aFRR_prices_DK1_2019.csv')
df_afrr = df_afrr.set_index(df_afrr['HourUTC'])
# special regulation
df_special = pd.read_csv('data/specialReg_2017-2019_dk1.csv',index_col=0)
# spot prices
df_spot=pd.read_csv('data/elspotprices.csv',sep=',')
df_spot = df_spot.set_index(df_spot['HourUTC'])

## Spot price plots

In [39]:
spot_prices = [df_spot['SpotPriceDKK'][t.strftime("%Y-%m-%d %H:%M")] for t in T]
go.Figure(go.Scatter(x=T,y=spot_prices),layout=dict(xaxis_title='Time',yaxis_title='Spot price [DKK/MWh]',yaxis_range=[-200,800]))

In [42]:
go.Figure(go.Scatter(x=list(range(len(T))),y=np.sort(spot_prices)[::-1]),
layout=dict(yaxis_range=[-200,800],yaxis_title='Spot price [DKK/MWh]',xaxis_title='Hours in simulation'))

## FCR Price plots

In [43]:
fcr_up = [df_fcr['FCR_UpPriceDKK'][t.strftime('%Y-%m-%d %H:%M')] for t in T]
fcr_down = [df_fcr['FCR_DownPriceDKK'][t.strftime('%Y-%m-%d %H:%M')] for t in T]

In [55]:
fig = go.Figure(layout=dict(xaxis_title='Time',yaxis_title='FCR price [DKK/MW]',yaxis_range=[0,800],legend=dict(x=0.8,y=1)))
fig.add_trace(go.Scatter(x=T,y=fcr_up,name='FCR Up'))
fig.add_trace(go.Scatter(x=T,y=fcr_down, name='FCR Down'))

In [57]:
fig = go.Figure(layout=dict(xaxis_title='Hours in simulation',yaxis_title='FCR price [DKK/MW]',yaxis_range=[0,800],legend=dict(x=0.8,y=1)))
fig.add_trace(go.Scatter(x=list(range(len(T))),y=np.sort(fcr_up)[::-1],name='FCR Up'))
fig.add_trace(go.Scatter(x=list(range(len(T))),y=np.sort(fcr_down)[::-1], name='FCR Down'))

## aFRR plots